In [1]:
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf

In [2]:
class PositionalEncoding(tf.keras.layers.Layer):
  def __init__(self, position, d_model):
    super(PositionalEncoding, self).__init__()
    self.pos_encoding = self.positional_encoding(position, d_model)

  def get_angles(self, position, i, d_model):
    angles = 1 / tf.pow(10000, (2 * (i // 2)) / tf.cast(d_model, tf.float32))
    return position * angles

  def positional_encoding(self, position, d_model):
    angle_rads = self.get_angles(
        position=tf.range(position, dtype=tf.float32)[:, tf.newaxis],
        i=tf.range(d_model, dtype=tf.float32)[tf.newaxis, :],
        d_model=d_model)

    # 배열의 짝수 인덱스(2i)에는 사인 함수 적용
    sines = tf.math.sin(angle_rads[:, 0::2])

    # 배열의 홀수 인덱스(2i+1)에는 코사인 함수 적용
    cosines = tf.math.cos(angle_rads[:, 1::2])

    angle_rads = np.zeros(angle_rads.shape)
    angle_rads[:, 0::2] = sines
    angle_rads[:, 1::2] = cosines
    pos_encoding = tf.constant(angle_rads)
    pos_encoding = pos_encoding[tf.newaxis, ...]

    print(pos_encoding.shape)
    return tf.cast(pos_encoding, tf.float32)

  def call(self, inputs):
    return inputs + self.pos_encoding[:, :tf.shape(inputs)[1], :]

In [3]:
def scaled_dot_product_attention(query, key, value, mask):
  # query 크기 : (batch_size, num_heads, query의 문장 길이, d_model/num_heads)
  # key 크기 : (batch_size, num_heads, key의 문장 길이, d_model/num_heads)
  # value 크기 : (batch_size, num_heads, value의 문장 길이, d_model/num_heads)
  # padding_mask : (batch_size, 1, 1, key의 문장 길이)

  # Q와 K의 곱. 어텐션 스코어 행렬.
  matmul_qk = tf.matmul(query, key, transpose_b=True)

  # 스케일링
  # dk의 루트값으로 나눠준다.
  depth = tf.cast(tf.shape(key)[-1], tf.float32)
  logits = matmul_qk / tf.math.sqrt(depth)

  # 마스킹. 어텐션 스코어 행렬의 마스킹 할 위치에 매우 작은 음수값을 넣는다.
  # 매우 작은 값이므로 소프트맥스 함수를 지나면 행렬의 해당 위치의 값은 0이 된다.
  if mask is not None:
    logits += (mask * -1e9)

  # 소프트맥스 함수는 마지막 차원인 key의 문장 길이 방향으로 수행된다.
  # attention weight : (batch_size, num_heads, query의 문장 길이, key의 문장 길이)
  attention_weights = tf.nn.softmax(logits, axis=-1)

  # output : (batch_size, num_heads, query의 문장 길이, d_model/num_heads)
  output = tf.matmul(attention_weights, value)

  return output, attention_weights

In [4]:
class MultiHeadAttention(tf.keras.layers.Layer):

  def __init__(self, d_model, num_heads, name="multi_head_attention"):
    super(MultiHeadAttention, self).__init__(name=name)
    self.num_heads = num_heads
    self.d_model = d_model

    assert d_model % self.num_heads == 0

    # d_model을 num_heads로 나눈 값.
    # 논문 기준 : 64
    self.depth = d_model // self.num_heads

    # WQ, WK, WV에 해당하는 밀집층 정의
    self.query_dense = tf.keras.layers.Dense(units=d_model)
    self.key_dense = tf.keras.layers.Dense(units=d_model)
    self.value_dense = tf.keras.layers.Dense(units=d_model)

    # WO에 해당하는 밀집층 정의
    self.dense = tf.keras.layers.Dense(units=d_model)

  # num_heads 개수만큼 q, k, v를 split하는 함수
  def split_heads(self, inputs, batch_size):
    inputs = tf.reshape(
        inputs, shape=(batch_size, -1, self.num_heads, self.depth))
    return tf.transpose(inputs, perm=[0, 2, 1, 3])

  def call(self, inputs):
    query, key, value, mask = inputs['query'], inputs['key'], inputs[
        'value'], inputs['mask']
    batch_size = tf.shape(query)[0]

    # 1. WQ, WK, WV에 해당하는 밀집층 지나기
    # q : (batch_size, query의 문장 길이, d_model)
    # k : (batch_size, key의 문장 길이, d_model)
    # v : (batch_size, value의 문장 길이, d_model)
    # 참고) 인코더(k, v)-디코더(q) 어텐션에서는 query 길이와 key, value의 길이는 다를 수 있다.
    query = self.query_dense(query)
    key = self.key_dense(key)
    value = self.value_dense(value)

    # 2. 헤드 나누기
    # q : (batch_size, num_heads, query의 문장 길이, d_model/num_heads)
    # k : (batch_size, num_heads, key의 문장 길이, d_model/num_heads)
    # v : (batch_size, num_heads, value의 문장 길이, d_model/num_heads)
    query = self.split_heads(query, batch_size)
    key = self.split_heads(key, batch_size)
    value = self.split_heads(value, batch_size)

    # 3. 스케일드 닷 프로덕트 어텐션. 앞서 구현한 함수 사용.
    # (batch_size, num_heads, query의 문장 길이, d_model/num_heads)
    scaled_attention, _ = scaled_dot_product_attention(query, key, value, mask)
    # (batch_size, query의 문장 길이, num_heads, d_model/num_heads)
    scaled_attention = tf.transpose(scaled_attention, perm=[0, 2, 1, 3])

    # 4. 헤드 연결(concatenate)하기
    # (batch_size, query의 문장 길이, d_model)
    concat_attention = tf.reshape(scaled_attention,
                                  (batch_size, -1, self.d_model))

    # 5. WO에 해당하는 밀집층 지나기
    # (batch_size, query의 문장 길이, d_model)
    outputs = self.dense(concat_attention)

    return outputs

In [5]:
def create_padding_mask(x):
  mask = tf.cast(tf.math.equal(x, 0), tf.float32)
  # (batch_size, 1, 1, key의 문장 길이)
  return mask[:, tf.newaxis, tf.newaxis, :]

In [6]:
def encoder_layer(dff, d_model, num_heads, dropout, name="encoder_layer"):
  inputs = tf.keras.Input(shape=(None, d_model), name="inputs")

  # 인코더는 패딩 마스크 사용
  padding_mask = tf.keras.Input(shape=(1, 1, None), name="padding_mask")

  # 멀티-헤드 어텐션 (첫번째 서브층 / 셀프 어텐션)
  attention = MultiHeadAttention(
      d_model, num_heads, name="attention")({
          'query': inputs, 'key': inputs, 'value': inputs, # Q = K = V
          'mask': padding_mask # 패딩 마스크 사용
      })

  # 드롭아웃 + 잔차 연결과 층 정규화
  attention = tf.keras.layers.Dropout(rate=dropout)(attention)
  attention = tf.keras.layers.LayerNormalization(
      epsilon=1e-6)(inputs + attention)

  # 포지션 와이즈 피드 포워드 신경망 (두번째 서브층)
  outputs = tf.keras.layers.Dense(units=dff, activation='relu')(attention)
  outputs = tf.keras.layers.Dense(units=d_model)(outputs)

  # 드롭아웃 + 잔차 연결과 층 정규화
  outputs = tf.keras.layers.Dropout(rate=dropout)(outputs)
  outputs = tf.keras.layers.LayerNormalization(
      epsilon=1e-6)(attention + outputs)

  return tf.keras.Model(
      inputs=[inputs, padding_mask], outputs=outputs, name=name)

In [7]:
def encoder(vocab_size, num_layers, dff,
            d_model, num_heads, dropout,
            name="encoder"):
  inputs = tf.keras.Input(shape=(None,), name="inputs")

  # 인코더는 패딩 마스크 사용
  padding_mask = tf.keras.Input(shape=(1, 1, None), name="padding_mask")

  # 포지셔널 인코딩 + 드롭아웃
  embeddings = tf.keras.layers.Embedding(vocab_size, d_model)(inputs)
  embeddings *= tf.math.sqrt(tf.cast(d_model, tf.float32))
  embeddings = PositionalEncoding(vocab_size, d_model)(embeddings)
  outputs = tf.keras.layers.Dropout(rate=dropout)(embeddings)

  # 인코더를 num_layers개 쌓기
  for i in range(num_layers):
    outputs = encoder_layer(dff=dff, d_model=d_model, num_heads=num_heads,
        dropout=dropout, name="encoder_layer_{}".format(i),
    )([outputs, padding_mask])

  return tf.keras.Model(
      inputs=[inputs, padding_mask], outputs=outputs, name=name)

In [8]:
def create_look_ahead_mask(x):
  seq_len = tf.shape(x)[1]
  look_ahead_mask = 1 - tf.linalg.band_part(tf.ones((seq_len, seq_len)), -1, 0)
  padding_mask = create_padding_mask(x) # 패딩 마스크도 포함
  return tf.maximum(look_ahead_mask, padding_mask)

In [9]:
def decoder_layer(dff, d_model, num_heads, dropout, name="decoder_layer"):
  inputs = tf.keras.Input(shape=(None, d_model), name="inputs")
  enc_outputs = tf.keras.Input(shape=(None, d_model), name="encoder_outputs")

  # 룩어헤드 마스크(첫번째 서브층)
  look_ahead_mask = tf.keras.Input(
      shape=(1, None, None), name="look_ahead_mask")

  # 패딩 마스크(두번째 서브층)
  padding_mask = tf.keras.Input(shape=(1, 1, None), name='padding_mask')

  # 멀티-헤드 어텐션 (첫번째 서브층 / 마스크드 셀프 어텐션)
  attention1 = MultiHeadAttention(
      d_model, num_heads, name="attention_1")(inputs={
          'query': inputs, 'key': inputs, 'value': inputs, # Q = K = V
          'mask': look_ahead_mask # 룩어헤드 마스크
      })

  # 잔차 연결과 층 정규화
  attention1 = tf.keras.layers.LayerNormalization(
      epsilon=1e-6)(attention1 + inputs)

  # 멀티-헤드 어텐션 (두번째 서브층 / 디코더-인코더 어텐션)
  attention2 = MultiHeadAttention(
      d_model, num_heads, name="attention_2")(inputs={
          'query': attention1, 'key': enc_outputs, 'value': enc_outputs, # Q != K = V
          'mask': padding_mask # 패딩 마스크
      })

  # 드롭아웃 + 잔차 연결과 층 정규화
  attention2 = tf.keras.layers.Dropout(rate=dropout)(attention2)
  attention2 = tf.keras.layers.LayerNormalization(
      epsilon=1e-6)(attention2 + attention1)

  # 포지션 와이즈 피드 포워드 신경망 (세번째 서브층)
  outputs = tf.keras.layers.Dense(units=dff, activation='relu')(attention2)
  outputs = tf.keras.layers.Dense(units=d_model)(outputs)

  # 드롭아웃 + 잔차 연결과 층 정규화
  outputs = tf.keras.layers.Dropout(rate=dropout)(outputs)
  outputs = tf.keras.layers.LayerNormalization(
      epsilon=1e-6)(outputs + attention2)

  return tf.keras.Model(
      inputs=[inputs, enc_outputs, look_ahead_mask, padding_mask],
      outputs=outputs,
      name=name)

In [10]:
def decoder(vocab_size, num_layers, dff,
            d_model, num_heads, dropout,
            name='decoder'):
  inputs = tf.keras.Input(shape=(None,), name='inputs')
  enc_outputs = tf.keras.Input(shape=(None, d_model), name='encoder_outputs')

  # 디코더는 룩어헤드 마스크(첫번째 서브층)와 패딩 마스크(두번째 서브층) 둘 다 사용.
  look_ahead_mask = tf.keras.Input(
      shape=(1, None, None), name='look_ahead_mask')
  padding_mask = tf.keras.Input(shape=(1, 1, None), name='padding_mask')

  # 포지셔널 인코딩 + 드롭아웃
  embeddings = tf.keras.layers.Embedding(vocab_size, d_model)(inputs)
  embeddings *= tf.math.sqrt(tf.cast(d_model, tf.float32))
  embeddings = PositionalEncoding(vocab_size, d_model)(embeddings)
  outputs = tf.keras.layers.Dropout(rate=dropout)(embeddings)

  # 디코더를 num_layers개 쌓기
  for i in range(num_layers):
    outputs = decoder_layer(dff=dff, d_model=d_model, num_heads=num_heads,
        dropout=dropout, name='decoder_layer_{}'.format(i),
    )(inputs=[outputs, enc_outputs, look_ahead_mask, padding_mask])

  return tf.keras.Model(
      inputs=[inputs, enc_outputs, look_ahead_mask, padding_mask],
      outputs=outputs,
      name=name)

In [11]:
def transformer(vocab_size, num_layers, dff,
                d_model, num_heads, dropout,
                name="transformer"):

  # 인코더의 입력
  inputs = tf.keras.Input(shape=(None,), name="inputs")

  # 디코더의 입력
  dec_inputs = tf.keras.Input(shape=(None,), name="dec_inputs")

  # 인코더의 패딩 마스크
  enc_padding_mask = tf.keras.layers.Lambda(
      create_padding_mask, output_shape=(1, 1, None),
      name='enc_padding_mask')(inputs)

  # 디코더의 룩어헤드 마스크(첫번째 서브층)
  look_ahead_mask = tf.keras.layers.Lambda(
      create_look_ahead_mask, output_shape=(1, None, None),
      name='look_ahead_mask')(dec_inputs)

  # 디코더의 패딩 마스크(두번째 서브층)
  dec_padding_mask = tf.keras.layers.Lambda(
      create_padding_mask, output_shape=(1, 1, None),
      name='dec_padding_mask')(inputs)

  # 인코더의 출력은 enc_outputs. 디코더로 전달된다.
  enc_outputs = encoder(vocab_size=vocab_size, num_layers=num_layers, dff=dff,
      d_model=d_model, num_heads=num_heads, dropout=dropout,
  )(inputs=[inputs, enc_padding_mask]) # 인코더의 입력은 입력 문장과 패딩 마스크

  # 디코더의 출력은 dec_outputs. 출력층으로 전달된다.
  dec_outputs = decoder(vocab_size=vocab_size, num_layers=num_layers, dff=dff,
      d_model=d_model, num_heads=num_heads, dropout=dropout,
  )(inputs=[dec_inputs, enc_outputs, look_ahead_mask, dec_padding_mask])

  # 다음 단어 예측을 위한 출력층
  outputs = tf.keras.layers.Dense(units=vocab_size, name="outputs")(dec_outputs)

  return tf.keras.Model(inputs=[inputs, dec_inputs], outputs=outputs, name=name)

In [12]:
class CustomSchedule(tf.keras.optimizers.schedules.LearningRateSchedule):

  def __init__(self, d_model, warmup_steps=4000):
    super(CustomSchedule, self).__init__()
    self.d_model = d_model
    self.d_model = tf.cast(self.d_model, tf.float32)
    self.warmup_steps = warmup_steps

  def __call__(self, step):
    arg1 = tf.math.rsqrt(step)
    arg2 = step * (self.warmup_steps**-1.5)

    return tf.math.rsqrt(self.d_model) * tf.math.minimum(arg1, arg2)

In [15]:
import pandas as pd
import json

with open('KorQuAD_v1.0_train.json') as json_file:
    json_obj = json.load(json_file)

In [17]:
len(json_obj['data'])

1420

In [35]:
q_a_dict = []

for data in json_obj['data']:
    for paragraph in data['paragraphs']:
        for qa in paragraph['qas']:
            q_a_dict.append({
                'Q': qa['question'],
                'A': qa['answers'][0]['text']
            })

{'answers': [{'text': '교향곡', 'answer_start': 54}], 'id': '6566495-0-0', 'question': '바그너는 괴테의 파우스트를 읽고 무엇을 쓰고자 했는가?'}
{'answers': [{'text': '1악장', 'answer_start': 421}], 'id': '6566495-0-1', 'question': '바그너는 교향곡 작곡을 어디까지 쓴 뒤에 중단했는가?'}
{'answers': [{'text': '베토벤의 교향곡 9번', 'answer_start': 194}], 'id': '6566495-0-2', 'question': '바그너가 파우스트 서곡을 쓸 때 어떤 곡의 영향을 받았는가?'}
{'answers': [{'text': '파우스트', 'answer_start': 15}], 'id': '6566518-0-0', 'question': '1839년 바그너가 교향곡의 소재로 쓰려고 했던 책은?'}
{'answers': [{'text': '합창교향곡', 'answer_start': 354}], 'id': '6566518-0-1', 'question': '파우스트 서곡의 라단조 조성이 영향을 받은 베토벤의 곡은?'}
{'answers': [{'text': '1839', 'answer_start': 0}], 'id': '5917067-0-0', 'question': '바그너가 파우스트를 처음으로 읽은 년도는?'}
{'answers': [{'text': '파리', 'answer_start': 410}], 'id': '5917067-0-1', 'question': '바그너가 처음 교향곡 작곡을 한 장소는?'}
{'answers': [{'text': '드레스덴', 'answer_start': 534}], 'id': '5917067-0-2', 'question': '바그너의 1악장의 초연은 어디서 연주되었는가?'}
{'answers': [{'text': '한스 폰 뷜로', 'answer_start': 402}], 

{'answers': [{'text': '전자 설비, 조선, 자동차', 'answer_start': 75}], 'id': '6480978-2-2', 'question': '경단연기계클럽에서 중점적으로 보도한 주제들은?'}
{'answers': [{'text': '경단연기계클럽', 'answer_start': 32}], 'id': '6480979-2-0', 'question': '일본 경제 단체 연합회의 요구로 해체된 곳은?'}
{'answers': [{'text': '자동차산업기자회', 'answer_start': 291}], 'id': '6480979-2-1', 'question': '자동차 업계가 만든 기자클럽의 이름은?'}
{'answers': [{'text': '1999년', 'answer_start': 0}], 'id': '6480979-2-2', 'question': '경단연기계클럽이 해체된 년도는?'}
{'answers': [{'text': '허리띠', 'answer_start': 74}], 'id': '6570759-0-0', 'question': '데스몬드 도스는 교회의 창문을 갈던 중 차에 깔린 남자를 발견하고 그를 지혈하기 위해 무엇을 사용했는가?'}
{'answers': [{'text': '도로시 쉬트', 'answer_start': 97}], 'id': '6570759-0-1', 'question': '데스몬드 도스는 병원에서 간호사 누구에게 허리띠를 부탁했는가?'}
{'answers': [{'text': '해롤드 도스', 'answer_start': 295}], 'id': '6570759-0-2', 'question': '데스몬드 도스의 형은 누구인가?'}
{'answers': [{'text': '데스몬드 도스', 'answer_start': 0}], 'id': '6570833-0-0', 'question': '차에 깔린 남자를 병원으로 데려가 목숨을 구한 사람은?'}
{'answers': [{'text': '간호사', 'answer_

{'answers': [{'text': '포츠머스', 'answer_start': 484}], 'id': '6502151-3-2', 'question': '1926-27 시즌 잉글랜드 2부 리그에서 2위를 차지한 팀은?'}
{'answers': [{'text': '0-1', 'answer_start': 47}], 'id': '6529318-3-0', 'question': '1926년 FA컵 결승전 스코어는 몇 대 몇이었는가?'}
{'answers': [{'text': '15분', 'answer_start': 305}], 'id': '6529318-3-1', 'question': '1926-27 시즌의 승격 경쟁에서 포츠머스의 경기 지연 시간은 얼마였는가?'}
{'answers': [{'text': '골 평균차', 'answer_start': 366}], 'id': '6529318-3-2', 'question': '1926-27 시즌에 적용되어 총 실점 수와 득점 수를 나누는 방법의 룰은 무엇인가?'}
{'answers': [{'text': '볼턴 원더러스', 'answer_start': 28}], 'id': '6465982-3-0', 'question': '1926년 경기에서 맨체스터 시티는 어느 팀에게 졌는가?'}
{'answers': [{'text': '1976 - 77시즌', 'answer_start': 453}], 'id': '6465982-3-1', 'question': '잉글랜드에서 골 평균차 대신 득실 차가 기준이 된 것은 어느 시즌부터인가?'}
{'answers': [{'text': '에버턴', 'answer_start': 123}], 'id': '6502151-4-0', 'question': '맨체스터 시티가 1933년 FA컵 결승에서 맞붙은 상대팀은?'}
{'answers': [{'text': '1934년', 'answer_start': 137}], 'id': '6502151-4-1', 'question': '맨체스터 시티가 두 번째 FA컵 

{'answers': [{'text': '2년', 'answer_start': 47}], 'id': '6534652-9-0', 'question': '하원의 435명의 개별 의원은 임기가 몇년인가? '}
{'answers': [{'text': '6년', 'answer_start': 270}], 'id': '6534652-9-1', 'question': '100명의 상원 의원은 전 주를 대표로 하며 임기는 몇년인가? '}
{'answers': [{'text': '양원의 동의', 'answer_start': 117}], 'id': '6529668-10-0', 'question': '미국 법률이 제정되기 위해 필요한 것은 무엇인가?'}
{'answers': [{'text': '하원', 'answer_start': 199}], 'id': '6529668-10-1', 'question': '연방 고위 공무원을 탄핵하고자 할 때 탄핵재판을 열 수 있는 권한을 가진 원은?'}
{'answers': [{'text': '세입 징수에 관한 법률안', 'answer_start': 316}], 'id': '6529668-10-2', 'question': '하원에서 먼저 제안되어야 하는 법률안은 무엇인가?'}
{'answers': [{'text': '상원', 'answer_start': 173}], 'id': '6462682-10-0', 'question': '하원이 연방 고위 공무원 탄핵재판을 실시할 수 있는 권한은 누구에게 있는가?'}
{'answers': [{'text': '의회의사당', 'answer_start': 536}], 'id': '6462682-10-1', 'question': '의회가 열리는 곳은?'}
{'answers': [{'text': '상원', 'answer_start': 173}], 'id': '6534652-10-0', 'question': '하원이 연방 고위 공무원을 탄핵하고자 할 때 탄핵재판을 열 수 있는 권한을 갖는 것은? '}
{'answers':

{'answers': [{'text': '파코 에레라', 'answer_start': 134}], 'id': '6518223-6-0', 'question': '2010년 셀타 비고에 새롭게 부임한 감독은?'}
{'answers': [{'text': '갈리시아', 'answer_start': 242}], 'id': '6518223-6-1', 'question': '셀타 비고 1군 선수들 대부분의 출신지는?'}
{'answers': [{'text': '러시아', 'answer_start': 0}], 'id': '6445485-7-0', 'question': '발레리 카르핀은 어느 나라 출신인가?'}
{'answers': [{'text': '수비형 미드필더', 'answer_start': 64}], 'id': '6445485-7-1', 'question': '클로드 마켈켈레의 포지션은 무엇인가?'}
{'answers': [{'text': '박주영', 'answer_start': 377}], 'id': '6445485-7-2', 'question': '2012~2013 시즌 대한민국 출신의 셀타 비고 선수는 누구인가?'}
{'answers': [{'text': '클로드 마켈켈레', 'answer_start': 83}], 'id': '6532287-7-0', 'question': '셀타 비고 출신으로 수비형 미드필더 중 최고로 꼽히는 사람은 누구인가?'}
{'answers': [{'text': '박주영', 'answer_start': 377}], 'id': '6532287-7-1', 'question': '우리나라 축국 선수로 2012년에서 2013년 시즌에 셀타 비고에서 활약한 사람은 누구인가?'}
{'answers': [{'text': '미도', 'answer_start': 141}], 'id': '6518223-7-0', 'question': '셀타 비고를 거쳐간 선수 중 이영표와 토튼햄에서 함께 뛴 이는?'}
{'answers': [{'text': '박주영', 

...

{'answers': [{'text': '1969년 4월', 'answer_start': 159}], 'id': '6543751-0-1', 'question': '육영수가 육영재단을 설립한 것은 언제인가?'}
{'answers': [{'text': '어깨동무', 'answer_start': 268}], 'id': '6543751-0-2', 'question': '육영수가 직접 발간한 소년소녀 잡지의 제목은 무엇인가?'}
{'answers': [{'text': '문세광', 'answer_start': 75}], 'id': '6543705-1-0', 'question': '1974년 장충동 국립극장에서 육영수를 암살한 사람은 누구인가?'}
{'answers': [{'text': '박종규', 'answer_start': 127}], 'id': '6543705-1-1', 'question': '문세광이 처음으로 총을 쏘자 이를 저지하기 위해 뛰쳐나간 경호실장은 누구인가?'}
{'answers': [{'text': '장봉화', 'answer_start': 205}], 'id': '6543705-1-2', 'question': '문세광과 경호원들의 총격전으로 사망한 성동여자실업고등학교 학생은 누구인가?'}
{'answers': [{'text': '광복절 기념식장', 'answer_start': 41}], 'id': '5834598-1-0', 'question': '1974년 육영수가 암살당한 장소는?'}
{'answers': [{'text': '문세광', 'answer_start': 75}], 'id': '5834598-1-1', 'question': '박정희 저격 미수 사건을 일으키고 육영수를 암살한 인물은 누구인가?'}
{'answers': [{'text': '장봉화', 'answer_start': 205}], 'id': '5834598-1-2', 'question': '범인과 경호원들간의 총격전으로 사망한 민간인의 이름은?'}
{'answers': [{'text':

{'answers': [{'text': '128.11점', 'answer_start': 115}], 'id': '6482022-6-1', 'question': '2차 그랑프리 컵 오브 차이나에서 김연아가 프리스케이팅에서 얻은 점수는?'}
{'answers': [{'text': '5연속', 'answer_start': 600}], 'id': '6482022-6-2', 'question': '2008년 컵 오브 차이나의 우승으로 김연아는 그랑프리 대회 몇 연속 우승을 달성하였는가?'}
{'answers': [{'text': '63.64', 'answer_start': 45}], 'id': '6511758-6-0', 'question': '11월에 열린 2차 그랑프리 컵 오브 차이나에 출전한 김연아는 쇼트 프로그램에서 몇점을 기록하였나?'}
{'answers': [{'text': '4.34', 'answer_start': 65}], 'id': '6511758-6-1', 'question': '11월에 열린 2차 그랑프리 컵 오브 차이나에 출전한 김연ㅇ아는 쇼트 프로그램에서 안도 미키를 몇점 차이로 눌렀나?'}
{'answers': [{'text': '20.87', 'answer_start': 234}], 'id': '6511758-6-2', 'question': '총점 191.75점으로 2위의 안도 미키를 몇점 차이로 누르고 우승했나?'}
{'answers': [{'text': '총점 191.75점', 'answer_start': 210}], 'id': '6269375-6-0', 'question': '김연아가 11월에 열린 그랑프리 컵 오브 차이나에서의 최종성적은?'}
{'answers': [{'text': '그랑프리 대회 5연속 우승', 'answer_start': 592}], 'id': '6269375-6-1', 'question': '2008년 컵 오브 차이나에서 김연아의 연속 우승횟수는?'}
{'answers': [{'text': '1회전', 'answer

{'answers': [{'text': '호놀룰루', 'answer_start': 283}], 'id': '6546926-8-1', 'question': '장원삼 대표와 티모시 대표는 제10차 SMA 체결을 어디서 진행하였는가?'}
{'answers': [{'text': '제주특별자치도', 'answer_start': 23}], 'id': '6580768-9-0', 'question': '제10차 방위비분담협상의 2차 회의가 진행된 곳은 어디인가?'}
{'answers': [{'text': '미국 국무부 청사', 'answer_start': 304}], 'id': '6580768-9-1', 'question': '5월 14일~ 15일에 있었던 제10차 방위비분담협상의 3차 회의가 열렸던 장소는 어디인가?'}
{'answers': [{'text': '안보 무임승차론', 'answer_start': 62}], 'id': '6580792-9-0', 'question': '트럼프가 전략자산 전개 비용을 한국이 부담해야 한다고 주장하면서 제기하는 이론은?'}
{'answers': [{'text': '한국', 'answer_start': 109}], 'id': '6580792-9-1', 'question': '방위비분담협정은 어디까지나 주한미군 주둔 비용에 관한 협상이라고 선을 그은 나라는?'}
{'answers': [{'text': '미국', 'answer_start': 304}], 'id': '6546926-9-0', 'question': '5월 14일~15일에 진행한 SMA 3차 회의는 어느 나라에서 했는가?'}
{'answers': [{'text': '4월', 'answer_start': 0}], 'id': '6546926-9-1', 'question': '제주도에서 진행된 SMA 2차 회의는 몇 월에 이루어 졌는가?'}
{'answers': [{'text': '9월', 'answer_start': 104}], 'id': '6580768-10-0', 'questi

{'answers': [{'text': '산업부', 'answer_start': 438}], 'id': '6580768-81-0', 'question': '2018년 2월 12일 국회에 제2의 사드 보복을 방지하기 위해 ISDS 개선을 요구하겠다고 밝힌 부처는 어디인가?'}
{'answers': [{'text': '2년', 'answer_start': 370}], 'id': '6580768-81-1', 'question': '한중FTA 발효 후 서비스, 투자 분야 협상의 개시를 몇 년 안에 하기로 합의하였는가?'}
{'answers': [{'text': '13억 5000만 달러', 'answer_start': 45}], 'id': '6580792-81-0', 'question': '한중 FTA가 체결될 당시 정부가 제조업 분야에서 수출 증가액으로 예상한 금액은?'}
{'answers': [{'text': '후속 협상', 'answer_start': 408}], 'id': '6580792-81-1', 'question': '한중 FTA 발효 2년 안에 서비스 투자 분야 협상을 개시하기로 합의한 것을 바탕으로 시작한 것은?'}
{'answers': [{'text': '투자자-국가분쟁해결제도', 'answer_start': 483}], 'id': '6546926-81-0', 'question': '산업부가 경제 보복을 방지하기위해 개선을 요구한 제도는 무엇인가?'}
{'answers': [{'text': '중국 비관세장벽', 'answer_start': 239}], 'id': '6546926-81-1', 'question': '한중 FTA 후 대중 수출이 적자를 유지한 이유는 무엇인가? '}
{'answers': [{'text': 'NAFTA', 'answer_start': 79}], 'id': '6580768-82-0', 'question': '트럼프가 대통령 후보시절부터 한미FTA와 함께 민주당 정부에서 체결한 실패한 협상으로 평가한 것은 무엇인가?'}
{'an

{'answers': [{'text': '임신한 암컷', 'answer_start': 325}], 'id': '6258454-6-0', 'question': '귀신고래 무리 중 가장 먼저 회유 경로를 출발하는 것은?'}
{'answers': [{'text': '2.5에서 3개월', 'answer_start': 414}], 'id': '6258454-6-1', 'question': '귀신고래 무리가 출생지로 돌아가는 데 걸리는 기간은?'}
{'answers': [{'text': '귀신고래', 'answer_start': 3}], 'id': '6490005-6-0', 'question': '주로 먹이 등을 위해 얕은 바다의 해안가를 따라 서식하는 고래는?'}
{'answers': [{'text': '2.5에서 3개월', 'answer_start': 414}], 'id': '6490005-6-1', 'question': '귀신고래가 회유에 걸리는 기간은?'}
{'answers': [{'text': '2만 킬로미터', 'answer_start': 154}], 'id': '6487767-6-0', 'question': '귀신고래의 연간 회유 거리는 얼마 이상인가?'}
{'answers': [{'text': '짝짓기와 번식', 'answer_start': 109}], 'id': '6487767-6-1', 'question': '귀신고래는 무엇을 위해 회유 경로의 최남단 지역으로 이동하는가?'}
{'answers': [{'text': '임신한 암컷', 'answer_start': 325}], 'id': '6487767-6-2', 'question': '귀신고래 중 가을에 가장 먼저 이동하는 것은?'}
{'answers': [{'text': '한국계 귀신고래', 'answer_start': 47}], 'id': '6258454-7-0', 'question': '북서태평양 개체군의 다른 이름은?'}
{'answers': [{'text': '로이 앤드류스', 'answer_st

In [38]:
train_data = pd.DataFrame.from_dict(q_a_dict)

In [39]:
train_data

Q  \
0                         바그너는 괴테의 파우스트를 읽고 무엇을 쓰고자 했는가?   
1                          바그너는 교향곡 작곡을 어디까지 쓴 뒤에 중단했는가?   
2                      바그너가 파우스트 서곡을 쓸 때 어떤 곡의 영향을 받았는가?   
3                         1839년 바그너가 교향곡의 소재로 쓰려고 했던 책은?   
4                       파우스트 서곡의 라단조 조성이 영향을 받은 베토벤의 곡은?   
...                                                  ...   
60402                   뉴델리 메탈로 베타락마제가 처음 감염 된 지역은 어디인가?   
60403        균은 유전자를 균에게 전달 할 수있는데 이러한 현상을 나타낸 용어는 무엇인가?   
60404  박테리아가 NDM-1 유전자를 가지고 있을때 발생하는 전파를 분석하기위해 사용된 영...   
60405         NDM-1 유전자를 가진 박테리아가 감수성을 보인 폴리믹슨 계열 항생제는?    
60406  2010년 8월, NDM-1 유전자를 가진 박테리아의 발생과 전파를 분석한 다국적 ...   

                                    A  
0                                 교향곡  
1                                 1악장  
2                         베토벤의 교향곡 9번  
3                                파우스트  
4                               합창교향곡  
...                               ...  
60402                              인도  
60403                          유전자 전달  
60404                             37건  
60405                            콜리스틴  
60406  The Lancet Infectious Diseases  

[60407 rows x 2 columns]

In [41]:
import re
questions = []
for sentence in train_data['Q']:
    # 구두점에 대해서 띄어쓰기
    # ex) 12시 땡! -> 12시 땡 !
    sentence = re.sub(r"([?.!,])", r" \1 ", sentence)
    sentence = sentence.strip()
    questions.append(sentence)
    
answers = []
for sentence in train_data['A']:
    # 구두점에 대해서 띄어쓰기
    # ex) 12시 땡! -> 12시 땡 !
    sentence = re.sub(r"([?.!,])", r" \1 ", sentence)
    sentence = sentence.strip()
    answers.append(sentence)

In [42]:
print(questions[:5])
print(answers[:5])

['바그너는 괴테의 파우스트를 읽고 무엇을 쓰고자 했는가 ?', '바그너는 교향곡 작곡을 어디까지 쓴 뒤에 중단했는가 ?', '바그너가 파우스트 서곡을 쓸 때 어떤 곡의 영향을 받았는가 ?', '1839년 바그너가 교향곡의 소재로 쓰려고 했던 책은 ?', '파우스트 서곡의 라단조 조성이 영향을 받은 베토벤의 곡은 ?']
['교향곡', '1악장', '베토벤의 교향곡 9번', '파우스트', '합창교향곡']


In [44]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import re
import urllib.request
import time
import tensorflow_datasets as tfds
import tensorflow as tf

tokenizer = tfds.deprecated.text.SubwordTextEncoder.build_from_corpus(
    questions + answers, target_vocab_size=2**13)

In [45]:
START_TOKEN, END_TOKEN = [tokenizer.vocab_size], [tokenizer.vocab_size + 1]

# 시작 토큰과 종료 토큰을 고려하여 단어 집합의 크기를 + 2
VOCAB_SIZE = tokenizer.vocab_size + 2

In [47]:
print('시작 토큰 번호 :',START_TOKEN)
print('종료 토큰 번호 :',END_TOKEN)
print('단어 집합의 크기 :',VOCAB_SIZE)

시작 토큰 번호 : [8173]
종료 토큰 번호 : [8174]
단어 집합의 크기 : 8175


In [48]:
# 최대 길이를 40으로 정의
MAX_LENGTH = 40

# 토큰화 / 정수 인코딩 / 시작 토큰과 종료 토큰 추가 / 패딩
def tokenize_and_filter(inputs, outputs):
  tokenized_inputs, tokenized_outputs = [], []

  for (sentence1, sentence2) in zip(inputs, outputs):
    # encode(토큰화 + 정수 인코딩), 시작 토큰과 종료 토큰 추가
    sentence1 = START_TOKEN + tokenizer.encode(sentence1) + END_TOKEN
    sentence2 = START_TOKEN + tokenizer.encode(sentence2) + END_TOKEN

    tokenized_inputs.append(sentence1)
    tokenized_outputs.append(sentence2)

  # 패딩
  tokenized_inputs = tf.keras.preprocessing.sequence.pad_sequences(
      tokenized_inputs, maxlen=MAX_LENGTH, padding='post')
  tokenized_outputs = tf.keras.preprocessing.sequence.pad_sequences(
      tokenized_outputs, maxlen=MAX_LENGTH, padding='post')

  return tokenized_inputs, tokenized_outputs

In [49]:
questions, answers = tokenize_and_filter(questions, answers)

In [50]:
print('질문 데이터의 크기(shape) :', questions.shape)
print('답변 데이터의 크기(shape) :', answers.shape)

질문 데이터의 크기(shape) : (60407, 40)
답변 데이터의 크기(shape) : (60407, 40)


In [51]:
# 텐서플로우 dataset을 이용하여 셔플(shuffle)을 수행하되, 배치 크기로 데이터를 묶는다.
# 또한 이 과정에서 교사 강요(teacher forcing)을 사용하기 위해서 디코더의 입력과 실제값 시퀀스를 구성한다.
BATCH_SIZE = 64
BUFFER_SIZE = 20000

# 디코더의 실제값 시퀀스에서는 시작 토큰을 제거해야 한다.
dataset = tf.data.Dataset.from_tensor_slices((
    {
        'inputs': questions,
        'dec_inputs': answers[:, :-1] # 디코더의 입력. 마지막 패딩 토큰이 제거된다.
    },
    {
        'outputs': answers[:, 1:]  # 맨 처음 토큰이 제거된다. 다시 말해 시작 토큰이 제거된다.
    },
))

dataset = dataset.cache()
dataset = dataset.shuffle(BUFFER_SIZE)
dataset = dataset.batch(BATCH_SIZE)
dataset = dataset.prefetch(tf.data.experimental.AUTOTUNE)

In [52]:
tf.keras.backend.clear_session()

# Hyper-parameters
D_MODEL = 256
NUM_LAYERS = 2
NUM_HEADS = 8
DFF = 512
DROPOUT = 0.1

model = transformer(
    vocab_size=VOCAB_SIZE,
    num_layers=NUM_LAYERS,
    dff=DFF,
    d_model=D_MODEL,
    num_heads=NUM_HEADS,
    dropout=DROPOUT)

(1, 8175, 256)
(1, 8175, 256)


In [53]:
def loss_function(y_true, y_pred):
  y_true = tf.reshape(y_true, shape=(-1, MAX_LENGTH - 1))

  loss = tf.keras.losses.SparseCategoricalCrossentropy(
      from_logits=True, reduction='none')(y_true, y_pred)

  mask = tf.cast(tf.not_equal(y_true, 0), tf.float32)
  loss = tf.multiply(loss, mask)

  return tf.reduce_mean(loss)

In [54]:
learning_rate = CustomSchedule(D_MODEL)

optimizer = tf.keras.optimizers.Adam(
    learning_rate, beta_1=0.9, beta_2=0.98, epsilon=1e-9)

def accuracy(y_true, y_pred):
  # 레이블의 크기는 (batch_size, MAX_LENGTH - 1)
  y_true = tf.reshape(y_true, shape=(-1, MAX_LENGTH - 1))
  return tf.keras.metrics.sparse_categorical_accuracy(y_true, y_pred)

model.compile(optimizer=optimizer, loss=loss_function, metrics=[accuracy])

In [55]:
model.summary()

Model: "transformer"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
inputs (InputLayer)             [(None, None)]       0                                            
__________________________________________________________________________________________________
dec_inputs (InputLayer)         [(None, None)]       0                                            
__________________________________________________________________________________________________
enc_padding_mask (Lambda)       (None, 1, 1, None)   0           inputs[0][0]                     
__________________________________________________________________________________________________
encoder (Functional)            (None, None, 256)    3147008     inputs[0][0]                     
                                                                 enc_padding_mask[0][0] 

In [56]:
EPOCHS = 50
model.fit(dataset, epochs=EPOCHS)

Epoch 1/50
168/944 [====>.........................] - ETA: 5:10 - loss: 0.9887 - accuracy: 0.0121

KeyboardInterrupt: 

In [ ]:
def evaluate(sentence):
  sentence = preprocess_sentence(sentence)

  sentence = tf.expand_dims(
      START_TOKEN + tokenizer.encode(sentence) + END_TOKEN, axis=0)

  output = tf.expand_dims(START_TOKEN, 0)

  # 디코더의 예측 시작
  for i in range(MAX_LENGTH):
    predictions = model(inputs=[sentence, output], training=False)

    # 현재(마지막) 시점의 예측 단어를 받아온다.
    predictions = predictions[:, -1:, :]
    predicted_id = tf.cast(tf.argmax(predictions, axis=-1), tf.int32)

    # 만약 마지막 시점의 예측 단어가 종료 토큰이라면 예측을 중단
    if tf.equal(predicted_id, END_TOKEN[0]):
      break

    # 마지막 시점의 예측 단어를 출력에 연결한다.
    # 이는 for문을 통해서 디코더의 입력으로 사용될 예정이다.
    output = tf.concat([output, predicted_id], axis=-1)

  return tf.squeeze(output, axis=0)

In [ ]:
def predict(sentence):
  prediction = evaluate(sentence)

  predicted_sentence = tokenizer.decode(
      [i for i in prediction if i < tokenizer.vocab_size])

  print('Input: {}'.format(sentence))
  print('Output: {}'.format(predicted_sentence))

  return predicted_sentence

In [ ]:
def preprocess_sentence(sentence):
  sentence = re.sub(r"([?.!,])", r" \1 ", sentence)
  sentence = sentence.strip()
  return sentence

In [ ]:
output = predict("바그너는 괴테의 파우스트를 읽고 무엇을 쓰고자 했는가")